In [45]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.metrics import accuracy_score, roc_auc_score, silhouette_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
import statsmodels.formula.api as smf
import statsmodels.api as sm
from scipy.stats import chi2
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.lines as mlines
import plotly.express as px
import statsmodels.api as sm
import numpy as np
from scipy.stats import chi2
from sklearn.metrics import accuracy_score
from sklearn.covariance import MinCovDet

# =====================================
# Functions
# =====================================

def load_and_prepare_data(file_path):
    """Load and preprocess the dataset."""
    df = pd.read_csv(file_path)
    df = df.drop(columns=['Field of Study'])

    # Mappings
    education_mapping = {'High School': 1, 'PhD': 4, "Master's": 3, "Bachelor's": 2}
    growth_mapping = {'High': 3, 'Low': 1, "Medium": 2}
    influence_mapping = {'High': 3, 'Low': 1, "Medium": 2}
    gender_mapping = {'Male': 0, 'Female': 1}

    df['Education Level'] = df['Education Level'].map(education_mapping)
    df['Industry Growth Rate'] = df['Industry Growth Rate'].map(growth_mapping)
    df['Family Influence'] = df['Family Influence'].map(influence_mapping).fillna(0).astype(int)
    df['Gender'] = df['Gender'].map(gender_mapping)

    # Scale certain columns
    scaler = MinMaxScaler()
    ordinal_col = ['Skills Gap', 'Job Satisfaction', 'Work-Life Balance', 'Job Security', 'Professional Networks', 'Technology Adoption']
    df[ordinal_col] = scaler.fit_transform(df[ordinal_col])

    # Filter columns and rename
    target_column = 'Likely_to_Change_Occupation'
    filtered_columns = df.columns.difference(['Current Occupation', 'Career Change Interest'])
    filtered_df = df.loc[:, filtered_columns]
    filtered_df.columns = filtered_df.columns.str.replace(' ', '_').str.replace('-', '_')

    return df, filtered_df, target_column

def fit_logistic_regression(formula, train_df):
    """Fit and return a logistic regression model using statsmodels."""
    model = smf.logit(formula, data=train_df).fit()
    return model

def evaluate_model(model, train_df, test_df, target_column):
    """Evaluate the given model on train and test sets."""
    # Training predictions
    train_predictions = model.predict(train_df)
    train_preds_class = (train_predictions > 0.5).astype(int)
    train_accuracy = accuracy_score(train_df[target_column], train_preds_class)
    train_auc = roc_auc_score(train_df[target_column], train_predictions)

    # Testing predictions
    test_predictions = model.predict(test_df)
    test_preds_class = (test_predictions > 0.5).astype(int)
    test_accuracy = accuracy_score(test_df[target_column], test_preds_class)
    test_auc = roc_auc_score(test_df[target_column], test_predictions)

    return {
        'train_accuracy': train_accuracy,
        'train_auc': train_auc,
        'test_accuracy': test_accuracy,
        'test_auc': test_auc
    }

def fit_random_forest(X_train, y_train):
    """Fit a random forest classifier."""
    rf_model = RandomForestClassifier(random_state=42)
    rf_model.fit(X_train, y_train)
    return rf_model

def evaluate_random_forest(rf_model, X_test, y_test):
    """Evaluate the random forest model."""
    rf_probs = rf_model.predict_proba(X_test)[:, 1]
    rf_preds = (rf_probs > 0.5).astype(int)

    rf_accuracy = accuracy_score(y_test, rf_preds)
    rf_auc = roc_auc_score(y_test, rf_probs)
    return rf_accuracy, rf_auc

def detect_outliers(train_df, formula, target_column):
    """Detect outliers using Cook's distance, Mahalanobis distance, and MCD-based Mahalanobis distance,
    plot results with Plotly, and choose the best method based on training accuracy."""

    # Fit the model once on the full training set
    outlier_model = sm.Logit.from_formula(formula, data=train_df).fit(disp=0)

    # Compute Cook's Distance
    influence = outlier_model.get_influence()
    cooks_d = influence.cooks_distance[0]
    cooks_threshold = 4 / len(train_df)
    cooks_outliers = np.where(cooks_d > cooks_threshold)[0]

    # Compute Mahalanobis Distance
    X_train_values = train_df.drop(columns=[target_column]).values
    mean_vec = np.mean(X_train_values, axis=0)
    cov_mat = np.cov(X_train_values, rowvar=False)
    inv_cov_mat = np.linalg.inv(cov_mat)
    diff = X_train_values - mean_vec
    mahal_dist = np.sqrt(np.diag(diff @ inv_cov_mat @ diff.T))

    p = X_train_values.shape[1]
    cutoff = chi2.ppf(0.975, p)
    mahal_threshold = np.sqrt(cutoff)
    mahal_outliers = np.where(mahal_dist > mahal_threshold)[0]

    # Compute MCD-Based Mahalanobis Distance
    mcd = MinCovDet().fit(X_train_values)
    robust_mean = mcd.location_
    robust_cov_inv = np.linalg.inv(mcd.covariance_)
    diff_mcd = X_train_values - robust_mean
    mcd_mahal_dist = np.sqrt(np.diag(diff_mcd @ robust_cov_inv @ diff_mcd.T))
    mcd_threshold = np.sqrt(chi2.ppf(0.975, p))
    mcd_outliers = np.where(mcd_mahal_dist > mcd_threshold)[0]

    # Plot Cook's Distance
    fig_cooks = px.scatter(
        x=np.arange(len(cooks_d)),
        y=cooks_d,
        color=np.isin(np.arange(len(cooks_d)), cooks_outliers),
        title="Cook's Distance per Observation",
        labels={"x": "Observation Index", "y": "Cook's Distance", "color": "Is Outlier"}
    )
    fig_cooks.add_hline(y=cooks_threshold, line_dash="dash", line_color="red", annotation_text="Threshold")
    fig_cooks.show()

    # Plot Mahalanobis Distance
    fig_mahal = px.scatter(
        x=np.arange(len(mahal_dist)),
        y=mahal_dist,
        color=np.isin(np.arange(len(mahal_dist)), mahal_outliers),
        title="Mahalanobis Distance per Observation",
        labels={"x": "Observation Index", "y": "Mahalanobis Distance", "color": "Is Outlier"}
    )
    fig_mahal.add_hline(y=mahal_threshold, line_dash="dash", line_color="red", annotation_text="Threshold")
    fig_mahal.show()

    # Plot MCD Mahalanobis Distance
    fig_mcd = px.scatter(
        x=np.arange(len(mcd_mahal_dist)),
        y=mcd_mahal_dist,
        color=np.isin(np.arange(len(mcd_mahal_dist)), mcd_outliers),
        title="MCD Mahalanobis Distance per Observation",
        labels={"x": "Observation Index", "y": "MCD Mahalanobis Distance", "color": "Is Outlier"}
    )
    fig_mcd.add_hline(y=mcd_threshold, line_dash="dash", line_color="red", annotation_text="Threshold")
    fig_mcd.show()

    # ============================
    # Valutazione del metodo migliore
    # ============================
    # Funzione per calcolare l'accuratezza sul training dopo la rimozione degli outlier
    def retrain_and_score(removed_indices):
        clean_train_df = train_df.drop(index=train_df.index[removed_indices]).reset_index(drop=True)
        model = sm.Logit.from_formula(formula, data=clean_train_df).fit(disp=0)
        train_preds = (model.predict(clean_train_df) > 0.5).astype(int)
        acc = accuracy_score(clean_train_df[target_column], train_preds)
        return acc

    cooks_acc = retrain_and_score(cooks_outliers)
    mahal_acc = retrain_and_score(mahal_outliers)
    mcd_acc = retrain_and_score(mcd_outliers)

    print(f"Accuracy after removing Cook's outliers: {cooks_acc:.4f}")
    print(f"Accuracy after removing Mahalanobis outliers: {mahal_acc:.4f}")
    print(f"Accuracy after removing MCD outliers: {mcd_acc:.4f}")

    # Choose the best method
    accuracies = {"Cook's": cooks_acc, "Mahalanobis": mahal_acc, "MCD": mcd_acc}
    chosen_method = max(accuracies, key=accuracies.get)
    print(f"Chosen method: {chosen_method}")

    if chosen_method == "Cook's":
        chosen_outliers = cooks_outliers
    elif chosen_method == "Mahalanobis":
        chosen_outliers = mahal_outliers
    else:
        chosen_outliers = mcd_outliers

    print(f"Number of chosen outliers: {len(chosen_outliers)}")

    return chosen_outliers

def backward_elimination(data, formula, significance_level=0.1, t_stat_threshold=2):
    """Perform backward elimination for logistic regression."""
    while True:
        model = smf.logit(formula, data=data).fit(disp=False)
        
        coefficients = model.params
        std_errors = model.bse
        p_values = model.pvalues
        t_stats = (coefficients / std_errors).abs()

        stats_df = p_values.to_frame(name='p_value')
        stats_df['coeff'] = coefficients
        stats_df['stderr'] = std_errors
        stats_df['t_stat'] = t_stats

        # Exclude the intercept
        stats_df = stats_df.drop('Intercept', errors='ignore')

        # Identify variables to remove
        stats_to_remove = stats_df[(stats_df['p_value'] > significance_level) & 
                                   (stats_df['t_stat'] <= t_stat_threshold)]
        
        if stats_to_remove.empty:
            break
        
        feature_to_remove = stats_to_remove['p_value'].idxmax()
        print(f"Removing feature '{feature_to_remove}' with p-value {stats_df.loc[feature_to_remove, 'p_value']:.4f} "
              f"and t-stat {stats_df.loc[feature_to_remove, 't_stat']:.4f}")

        # Update formula
        formula = formula.replace(f"+ {feature_to_remove}", "").replace(f"{feature_to_remove} +", "").replace(feature_to_remove, "")
    
    return model, formula



In [46]:
# Load and prepare data
df, filtered_df, target_column = load_and_prepare_data("C:/Users/Fabio/Desktop/AMS/group/new_dataset/career_change_prediction_dataset.csv")

# Construct formula
independent_vars = " + ".join(col for col in filtered_df.columns if col != target_column)
formula = f"{target_column} ~ {independent_vars}"

# Split data
train_df, test_df = train_test_split(filtered_df, test_size=0.2, random_state=42)

# Initial Logistic Regression
logit_model = fit_logistic_regression(formula, train_df)
print("===== Logistic Regression Model (Training Set) =====")
print(logit_model.summary())
lr_eval = evaluate_model(logit_model, train_df, test_df, target_column)
print(f"Training Set - Accuracy: {lr_eval['train_accuracy']:.4f}, AUC: {lr_eval['train_auc']:.4f}")
print("===== Logistic Regression Model (Test Set) =====")
print(f"Test Set - Accuracy: {lr_eval['test_accuracy']:.4f}, AUC: {lr_eval['test_auc']:.4f}")

# Initial Random Forest
X = filtered_df.drop(columns=[target_column])
y = filtered_df[target_column]
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42, stratify=y)
rf_model = fit_random_forest(X_train, y_train)
rf_accuracy, rf_auc = evaluate_random_forest(rf_model, X_test, y_test)
print("===== Initial Random Forest Model =====")
print(f"Random Forest Accuracy: {rf_accuracy:.4f}")
print(f"Random Forest AUC: {rf_auc:.4f}")

# Outlier Detection con la funzione aggiornata
outlier_indices = detect_outliers(train_df, formula, target_column)
print(f"Number of potential outliers in training set: {len(outlier_indices)}")
clean_train_df = train_df.drop(index=train_df.index[outlier_indices]).reset_index(drop=True)
print(f"Training set size after outlier removal: {clean_train_df.shape[0]} rows")

# Logistic Regression after outlier removal
cleaned_logit = fit_logistic_regression(formula, clean_train_df)
print("===== Logistic Regression After Outlier Removal =====")
print(cleaned_logit.summary())
cleaned_lr_eval = evaluate_model(cleaned_logit, clean_train_df, test_df, target_column)
print("===== Logistic Regression Evaluation on Test Set =====")
print(f"Test Set - Accuracy: {cleaned_lr_eval['test_accuracy']:.4f}, AUC: {cleaned_lr_eval['test_auc']:.4f}")

# Random Forest after outlier removal
X_clean_train = clean_train_df.drop(columns=[target_column])
y_clean_train = clean_train_df[target_column]
rf_model_cleaned = fit_random_forest(X_clean_train, y_clean_train)
rf_accuracy_cleaned, rf_auc_cleaned = evaluate_random_forest(rf_model_cleaned, test_df.drop(columns=[target_column]), test_df[target_column])
print("===== Random Forest Evaluation on Test Set (After Outlier Removal) =====")
print(f"Test Set - Accuracy: {rf_accuracy_cleaned:.4f}, AUC: {rf_auc_cleaned:.4f}")

# Backward Elimination
print("===== Backward Elimination Process =====")
final_model, final_formula = backward_elimination(train_df, formula)
print("Final Model Formula:", final_formula)
print("===== Final Logistic Regression Model =====")
print(final_model.summary())
final_lr_eval = evaluate_model(final_model, train_df, test_df, target_column)
print("Final Model - Test Set Accuracy:", final_lr_eval['test_accuracy'])
print("Final Model - Test Set AUC:", final_lr_eval['test_auc'])

# Robust Logistic Regression
logit_model_robust = smf.logit(formula, data=train_df).fit(cov_type='HC1')
print("===== Robust Logistic Regression Model (Training Set) =====")
print(logit_model_robust.summary())
robust_eval = evaluate_model(logit_model_robust, train_df, test_df, target_column)
print("===== Robust Logistic Regression Model (Test Set) =====")
print(f"Test Set (Robust) - Accuracy: {robust_eval['test_accuracy']:.4f}, AUC: {robust_eval['test_auc']:.4f}")

Optimization terminated successfully.
         Current function value: 0.452018
         Iterations 6
===== Logistic Regression Model (Training Set) =====
                                Logit Regression Results                               
Dep. Variable:     Likely_to_Change_Occupation   No. Observations:                30755
Model:                                   Logit   Df Residuals:                    30735
Method:                                    MLE   Df Model:                           19
Date:                         mar, 17 dic 2024   Pseudo R-squ.:                  0.3370
Time:                                 22:19:42   Log-Likelihood:                -13902.
converged:                                True   LL-Null:                       -20969.
Covariance Type:                     nonrobust   LLR p-value:                     0.000
                             coef    std err          z      P>|z|      [0.025      0.975]
--------------------------------------------------

Accuracy after removing Cook's outliers: 0.8461
Accuracy after removing Mahalanobis outliers: 0.7728
Accuracy after removing MCD outliers: 0.7718
Chosen method: Cook's
Number of chosen outliers: 1924
Number of potential outliers in training set: 1924
Training set size after outlier removal: 28831 rows
Optimization terminated successfully.
         Current function value: 0.321427
         Iterations 7
===== Logistic Regression After Outlier Removal =====
                                Logit Regression Results                               
Dep. Variable:     Likely_to_Change_Occupation   No. Observations:                28831
Model:                                   Logit   Df Residuals:                    28811
Method:                                    MLE   Df Model:                           19
Date:                         mar, 17 dic 2024   Pseudo R-squ.:                  0.5312
Time:                                 22:20:00   Log-Likelihood:                -9267.1
converged:   

In [47]:
# Set R environment
'''#R

import os

# Imposta il percorso di R_HOME e aggiungi R al PATH
os.environ['R_HOME'] = r"C:\Program Files\R\R-4.4.0"  # Sostituisci con la tua versione di R
os.environ['PATH'] += os.pathsep + r"C:\Program Files\R\R-4.4.0\bin\x64"'''

'#R\n\nimport os\n\n# Imposta il percorso di R_HOME e aggiungi R al PATH\nos.environ[\'R_HOME\'] = r"C:\\Program Files\\R\\R-4.4.0"  # Sostituisci con la tua versione di R\nos.environ[\'PATH\'] += os.pathsep + r"C:\\Program Files\\R\\R-4.4.0\x08ind"'

In [48]:
# Testa l'importazione di rpy2
%load_ext rpy2.ipython

The rpy2.ipython extension is already loaded. To reload it, use:
  %reload_ext rpy2.ipython


In [49]:
import rpy2.robjects as ro
from rpy2.robjects import pandas2ri

pandas2ri.activate()
ro.globalenv['filtered_df'] = filtered_df

In [50]:
filtered_df = df.copy()
filtered_df['Current_Occupation'] = df['Current Occupation']  # Copia la colonna

filtered_df['Likely_to_Change_Occupation'] = df['Likely to Change Occupation']

filtered_df['Job_Satisfaction'] = df['Job Satisfaction']

filtered_df['Work_Life_Balance'] = df['Work-Life Balance']

from sklearn.preprocessing import StandardScaler

# Variabili da scalare
vars_to_scale = ['Age', 'Job_Satisfaction', 'Salary', 'Work_Life_Balance']

# Crea una copia del dataframe originale
scaled_df = filtered_df.copy()

# Standardizza le variabili selezionate
scaler = StandardScaler()
scaled_df[vars_to_scale] = scaler.fit_transform(scaled_df[vars_to_scale])

# Trasferisci il dataframe scalato in R
import rpy2.robjects as ro
from rpy2.robjects import pandas2ri

pandas2ri.activate()
ro.globalenv['filtered_df'] = scaled_df

In [64]:
%%R
# Carica libreria lme4
library(lme4)

# Controlla le colonne scalate
print(summary(filtered_df))

# Formula del modello con variabili scalate
formula <- Likely_to_Change_Occupation ~ Age + Job_Satisfaction + Career_Change_Interest + Salary + Work_Life_Balance + 
            (1 | Current_Occupation)

# Adatta il modello GLMM (family = binomial per variabili binarie)
mixed_model <- glmer(formula, data = filtered_df, family = binomial(link = "logit"), 
                     control = glmerControl(optimizer = "bobyqa"))

# Stampa il sommario del modello
summary(mixed_model)

 Current_Occupation      Age               Gender       Years_of_Experience
 Length:38444       Min.   :-1.68823   Min.   :-1.004   Min.   :-1.69212   
 Class :character   1st Qu.:-0.82426   1st Qu.:-1.004   1st Qu.:-0.82651   
 Mode  :character   Median : 0.03971   Median : 0.996   Median : 0.03911   
                    Mean   : 0.00000   Mean   : 0.000   Mean   : 0.00000   
                    3rd Qu.: 0.90367   3rd Qu.: 0.996   3rd Qu.: 0.90472   
                    Max.   : 1.68124   Max.   : 0.996   Max.   : 1.68378   
 Education_Level   Industry_Growth_Rate Job_Satisfaction  Work_Life_Balance
 Min.   :-1.3438   Min.   :-1.238       Min.   :-1.5641   Min.   :-1.5689  
 1st Qu.:-1.3438   1st Qu.:-1.238       1st Qu.:-0.8674   1st Qu.:-0.8743  
 Median : 0.4385   Median :-0.012       Median : 0.1778   Median : 0.1678  
 Mean   : 0.0000   Mean   : 0.000       Mean   : 0.0000   Mean   : 0.0000  
 3rd Qu.: 1.3296   3rd Qu.: 1.214       3rd Qu.: 0.8746   3rd Qu.: 0.8624  
 Max.   : 1.